In [2]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from astropy.time import Time
from astroquery.jplhorizons import Horizons
import warnings

warnings.simplefilter('ignore', UserWarning)

plt.rcParams['animation.embed_limit'] = 100
plt.rcParams["animation.html"] = "jshtml"
plt.rcParams['axes.labelpad'] = 20

class Object:                   # define the objects: the Sun, Earth, Mercury, etc
    def __init__(self, name, rad, color, r, v):
        self.name = name
        self.r    = np.array(r, dtype=float)
        self.v    = np.array(v, dtype=float)
        self.vh    = np.array(v, dtype=float)
        self.xs = []
        self.ys = []
        self.plot = ax.scatter(r[0], r[1], color=color, s=rad**2, edgecolors=None, zorder=10)
        self.line, = ax.plot([], [], color=color, linewidth=1.4)

class SolarSystem:
    def __init__(self, thesun):
        self.thesun = thesun
        self.planets = []
        self.time = None
        self.timestamp = ax.text(.03, .94, 'Date: ', color='w', transform=ax.transAxes, fontsize='x-large')
    def add_planet(self, planet):
        self.planets.append(planet)
    def evolve_euler(self):           # evolve the trajectories
        dt = 10
        self.time += dt
        plots = []
        lines = []
        for p in self.planets:
            p.r += p.v * dt
            acc = -2.959e-4 * p.r / np.sum(p.r**2)**(3./2)  # in units of AU/day^2
            p.v += acc * dt
            p.xs.append(p.r[0])
            p.ys.append(p.r[1])
            p.plot.set_offsets(p.r[:2])
            p.line.set_xdata(p.xs)
            p.line.set_ydata(p.ys)
            plots.append(p.plot)
            lines.append(p.line)
        self.timestamp.set_text('Date: ' + Time(self.time, format='jd', out_subfmt='str').iso)
        return plots + lines + [self.timestamp]
    def evolve_verlet(self, dt):           # evolve the trajectories
        self.time += dt
        plots = []
        lines = []
        for p in self.planets:
            acc = -2.959e-4 * p.r / np.sum(p.r**2)**(3./2)  # in units of AU/day^2
            p.vh = p.v + 0.5* acc * dt
            p.r = p.r + p.vh*dt
            acc_new = -2.959e-4 * p.r / np.sum(p.r**2)**(3./2)
            p.v = p.vh + 0.5*acc_new*dt
            p.xs.append(p.r[0])
            p.ys.append(p.r[1])
            p.plot.set_offsets(p.r[:2])
            p.line.set_xdata(p.xs)
            p.line.set_ydata(p.ys)
            plots.append(p.plot)
            lines.append(p.line)
        self.timestamp.set_text('Date: ' + Time(self.time, format='jd', out_subfmt='str').iso)
        return plots + lines + [self.timestamp]

sim_start_date = "2024-04-01"     # simulating a solar system starting from this date
sim_duration = 200              # (int) simulation duration in days
frame_size = 20

plt.style.use('dark_background')
fig = plt.figure(figsize=[8, 8])
ax = plt.axes([0., 0., 1., 1.], xlim=(-frame_size, frame_size), ylim=(-frame_size, frame_size))
ax.set_aspect('equal')
ax.axis('off')



ss = SolarSystem(Object("Sun", 20, 'red', [0, 0, 0], [0, 0, 0]))
ss.time = Time(sim_start_date).jd
colors = ['gray', 'crimson', 'green', 'chocolate', 'sandybrown', 'gold', 'lightsteelblue']
sizes = [0.1, 0.35, 0.4, 0.25, 1, 0.75, 0.65]
names = ['Mercury', 'Venus', 'Earth', 'Mars', 'Jupyter', 'Saturn', 'Uranus']
texty = [.47, .73, 1, 1.5, 5.75, 10.75, 15]
for i, nasaid in enumerate([1, 2, 3, 4, 5, 6, 7]):  # The 1st, 2nd, 3rd, 4th planet in solar system
    obj = Horizons(id=nasaid, location="@sun", epochs=ss.time, id_type=None).vectors()
    ss.add_planet(Object(nasaid, 20 * sizes[i], colors[i], 
                         [np.double(obj[xi]) for xi in ['x', 'y', 'z']], 
                         [np.double(obj[vxi]) for vxi in ['vx', 'vy', 'vz']]))
    ax.text(0, - (texty[i] + 0.1), names[i], color=colors[i], zorder=1000, ha='center', fontsize='large')
def animate(i):
    return ss.evolve_verlet(dt=10) # dt = Nb jours par step



ani = animation.FuncAnimation(fig, animate, repeat=False, frames=sim_duration, blit=True, interval=20,)
display(ani)
plt.close()


